In [ ]:
#!pip install langchain openai chromadb tiktoken pypdf panel

In [3]:
import os 
# Load Environment Variables 
os.environ["OPENAI_API_KEY"] = "sk-proj-I0s6nSIKHJp0g6PyU6czT3BlbkFJxOakSbgWvxgWsdiYlh7w"
os.environ["USER_AGENT"] = "Shesh"
os.environ['LANGCHAIN_TRACING_V2'] = 'true'
os.environ['LANGCHAIN_ENDPOINT'] = 'https://api.smith.langchain.com'
os.environ['LANGCHAIN_API_KEY'] = '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'

In [4]:
from langchain.chains import RetrievalQA
from langchain.llms import OpenAI
from langchain.document_loaders import TextLoader
from langchain.document_loaders import PyPDFLoader
from langchain.text_splitter import CharacterTextSplitter
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import Chroma
import panel as pn
import tempfile
import os

/Users/shesh/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [5]:
pn.extension('texteditor', template="bootstrap", sizing_mode='stretch_width')
pn.state.template.param.update(
    main_max_width="690px",
    header_background="#F08080",
)

In [22]:
file_input = pn.widgets.FileInput(width=300)

openaikey = pn.widgets.PasswordInput(
    value="", placeholder="Enter your OpenAI API Key here...", width=300
)
prompt = pn.widgets.TextEditor(
    value="", placeholder="Enter your questions here...", height=160, toolbar=False
)
run_button = pn.widgets.Button(name="Run!")

select_k = pn.widgets.IntSlider(
    name="Number of relevant chunks", start=1, end=5, step=1, value=2
)
select_chain_type = pn.widgets.RadioButtonGroup(
    name='Chain type', 
    options=['stuff', 'map_reduce', "refine", "map_rerank"]
)

widgets = pn.Row(
    pn.Column(prompt, run_button, margin=5, width=300),
    pn.Column(
        pn.Card(
            "Chain type:",
            pn.Column(select_chain_type, select_k),
            title="Advanced settings", margin=10
        ), width=400
    )
)

widgets

Row(sizing_mode='stretch_width')
    [0] Column(margin=5, width=300)
        [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)
        [1] Button(name='Run!', sizing_mode='stretch_width')
    [1] Column(width=400)
        [0] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
            [0] Markdown(str, sizing_mode='stretch_width')
            [1] Column(sizing_mode='stretch_width')
                [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
                [1] IntSlider(end=5, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=2)

In [7]:
def qa(file, query, chain_type, k):
    # load document
    loader = PyPDFLoader(file)
    documents = loader.load()
    # split the documents into chunks
    text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)
    texts = text_splitter.split_documents(documents)
    # select which embeddings we want to use
    embeddings = OpenAIEmbeddings()
    # create the vectorestore to use as the index
    db = Chroma.from_documents(texts, embeddings)
    # expose this index in a retriever interface
    retriever = db.as_retriever(search_type="similarity", search_kwargs={"k": k})
    # create a chain to answer questions 
    qa = RetrievalQA.from_chain_type(
        llm=OpenAI(), chain_type=chain_type, retriever=retriever, return_source_documents=True)
    result = qa({"query": query})
    # print(result['result'])
    return result

In [ ]:
# result = qa("/Users/shesh/Downloads/Transactions.pdf", "When was GPT-2 created?", "map_reduce", 2)

In [18]:
convos = []  # store all panel objects in a list

def qa_result(_):
    os.environ["OPENAI_API_KEY"] = openaikey.value
    print(file_input.value)
    
    # save pdf file to a temp file 
    if file_input.value is not None:
        file_input.save("/tmp/temp.pdf")
    
        prompt_text = prompt.value
        if prompt_text:
            result = qa(file="/tmp/temp.pdf", query=prompt_text, chain_type=select_chain_type.value, k=select_k.value)
            print(result)
            convos.extend([
                pn.Row(
                    pn.panel("\U0001F60A", width=10),
                    prompt_text,
                    width=600
                ),
                pn.Row(
                    pn.panel("\U0001F916", width=10),
                    pn.Column(
                        result["result"],
                        "Relevant source text:",
                        pn.pane.Markdown('\n--------------------------------------------------------------------\n'.join(doc.page_content for doc in result["source_documents"])),
                        width=600
                    )
                )
            ])
    return pn.Column(*convos, margin=15, width=600, min_height=400)

In [9]:
qa_interactive = pn.panel(
    pn.bind(qa_result, run_button),
    loading_indicator=True,
)

None


In [10]:
output = pn.WidgetBox('*Output will show up here:*', qa_interactive, width=670, scroll=True)

In [24]:
# layout
pn.Column(
    pn.pane.Markdown("""
    ## \U0001F60A! Question Answering with your PDF file
    
    1) Upload a PDF. 2) Enter OpenAI API key. This costs $. Set up billing at [OpenAI](https://platform.openai.com/account). 3) Type a question and click "Run"

    ### Note

    1. ** Do not ** upload PDF with sensitive & personal information.
    2. Upload smaller PDF file size (< 4MB).
    
    """),
    pn.Row(file_input,openaikey),
    output,
    widgets

).servable()

Column(sizing_mode='stretch_width')
    [0] Markdown(str, sizing_mode='stretch_width')
    [1] Row(sizing_mode='stretch_width')
        [0] FileInput(width=300)
        [1] PasswordInput(placeholder='Enter your OpenAI A...)
    [2] WidgetBox(scroll=True, width=670)
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] ParamFunction(function, _pane=Column, defer_load=False, loading_indicator=True, sizing_mode='stretch_width')
    [3] Row(sizing_mode='stretch_width')
        [0] Column(margin=5, width=300)
            [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)
            [1] Button(name='Run!', sizing_mode='stretch_width')
        [1] Column(width=400)
            [0] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
                [0] Markdown(str, sizing_mode='stretch_width')
                [1] Column(sizing_mode='stretch_width')
                    [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
                    [1] IntSlider(end=5, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=2)

In [ ]:
# from langchain.chains.question_answering import load_qa_chain

# # load document
# loader = PyPDFLoader("/Users/shesh/Downloads/Transactions.pdf")
# documents = loader.load()

# ### For multiple documents 
# # loaders = [....]
# # documents = []
# # for loader in loaders:
# #     documents.extend(loader.load())

# chain = load_qa_chain(llm=OpenAI(), chain_type="map_reduce")
# query = "Where can I read about Making B-trees reliable?"
# chain.run(input_documents=documents, question=query)

In [ ]:
# # load document
# loader = PyPDFLoader("/Users/shesh/Downloads/Transactions.pdf")
# documents = loader.load()
# # split the documents into chunks
# text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)
# texts = text_splitter.split_documents(documents)
# # select which embeddings we want to use
# embeddings = OpenAIEmbeddings()
# # create the vectorestore to use as the index
# db = Chroma.from_documents(texts, embeddings)
# # expose this index in a retriever interface
# retriever = db.as_retriever(search_type="similarity", search_kwargs={"k":2})
# # create a chain to answer questions 
# qa = RetrievalQA.from_chain_type(
#     llm=OpenAI(), chain_type="stuff", retriever=retriever, return_source_documents=True, verbose=True)
# query = "what is the need for multi-object transactions?"
# result = qa({"query": query})

# retriever.get_relevant_documents(query)

# result